In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!pip install optuna optuna-dashboard
!pip install git+https://github.com/R-N/ml-utility-loss
!pip install git+https://github.com/R-N/ml-utility-loss --force-reinstall --no-deps

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 409.6/409.6 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.8/5.8 MB 60.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 226.8/226.8 kB 17.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 90.2/90.2 kB 10.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.7/78.7 kB 8.7 MB/s eta 0:00:00
  Cloning https://github.com/R-N/ml-utility-loss to /tmp/pip-req-build-5hq336xh
  Running command git clone --filter=blob:none --quiet https://github.com/R-N/ml-utility-loss /tmp/pip-req-build-5hq336xh
  Resolved https://github.com/R-N/ml-utility-loss to commit 88cad1fe670a454c22556ffab0b88ff417a72048
  Preparing metadata (setup.py) ... done
  Cloning https://github.com/R-N/torchtext (to revision 0.6.1) to /tmp/pip-install-bzeaekxa/torchtext_3c535108e57e4c20b0d9b110ebd7244b
  Running command git clone --filter=blob:none --quiet https://github.com/R-N/torchtext /tmp/pip-install-bzeaekxa/to

In [ ]:
%cd /content
!curl -Ls https://github.com/ekzhang/bore/releases/download/v0.4.0/bore-v0.4.0-x86_64-unknown-linux-musl.tar.gz | tar zx -C /usr/bin
!curl -Lo /usr/bin/cloudflared https://github.com/cloudflare/cloudflared/releases/latest/download/cloudflared-linux-amd64 && chmod +x /usr/bin/cloudflared

/content
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100 34.7M  100 34.7M    0     0  50.0M      0 --:--:-- --:--:-- --:--:--  104M


In [ ]:
datasets = [
    "insurance",
    "treatment",
    "contraceptive"
]

model_dir = "/content/drive/MyDrive/rizqinur2010/Documents/ITS/Tesis/Model/"

In [ ]:
import pandas as pd
import numpy as np
import json
import os

dataset_dir = "datasets"
dataset_name = "treatment"


In [409]:
from ml_utility_loss.util import mkdir

model_name = "realtabformer"
df_name = "4"
model_subdir = "mean-best-disc-model"
#model_name_2 = f"{model_name}_{dataset_name}_{df_name}"
model_dir_2 = os.path.join(model_dir, model_name, dataset_name, str(df_name))
mkdir(model_dir_2)
params_path = os.path.join(model_dir_2, f"params.json")

In [410]:
print(model_dir_2)

/content/drive/MyDrive/rizqinur2010/Documents/ITS/Tesis/Model/realtabformer/treatment/4


In [411]:

from ml_utility_loss.tuning import create_objective
import ml_utility_loss.synthesizers.realtabformer.params as PARAMS
from ml_utility_loss.util import filter_dict_2, filter_dict
from copy import deepcopy

params = getattr(PARAMS, dataset_name).BEST

model_params={
    **params,
}

model_params["epochs"] = min(model_params.pop("epochs", 100), 100)

model_params_ = deepcopy(model_params)

In [412]:
from ml_utility_loss.synthesizers.realtabformer.wrapper import REaLTabFormer
from ml_utility_loss.synthesizers.realtabformer.params.default import GPT2_PARAMS, REALTABFORMER_PARAMS

from transformers.models.gpt2 import GPT2Config

num_bootstrap = model_params.pop("num_bootstrap", 100)

gpt2_params = filter_dict(model_params, GPT2_PARAMS)
realtabformer_params = filter_dict(model_params, REALTABFORMER_PARAMS)

# Non-relational or parent table.
rtf_model = REaLTabFormer(
    tabular_config=GPT2Config(**gpt2_params),
    **realtabformer_params
)

rtf_model.experiment_id = str(df_name)


In [413]:
model_dir_3 = f"{model_dir_2}/{df_name}"
rtf_model = rtf_model.load_from_dir(
    model_dir_3,
    config_file="rtf_config.json",
    model_file=f"{model_subdir}/pytorch_model.bin"
)

In [414]:
text_embedding = rtf_model.model.transformer.wte
position_embedding = rtf_model.model.transformer.wpe

In [415]:
model_dir_4 = f"{model_dir_3}/{model_subdir}"

In [416]:
import torch
import os
from copy import deepcopy

torch.save(text_embedding, os.path.join(model_dir_4, "text_embedding.pt"))
torch.save(deepcopy(text_embedding.state_dict()), os.path.join(model_dir_4, "text_embedding.states.pt"))

In [417]:
import torch
import os
from copy import deepcopy

torch.save(position_embedding, os.path.join(model_dir_4, "position_embedding.pt"))
torch.save(deepcopy(position_embedding.state_dict()), os.path.join(model_dir_4, "position_embedding.states.pt"))

In [418]:
text_embedding.weight.shape[-1]

768